In [37]:
# importing required libraries 

import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt 
import numpy as np
from sklearn.model_selection import train_test_split
import warnings
import plotly.express as px
import plotly.graph_objects as go

warnings.simplefilter("ignore")

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [38]:

# read in data csv/frames

circuits_df = pd.read_csv("data/circuits.csv")
constructor_results_df = pd.read_csv("data/constructor_results.csv")
constructors_df = pd.read_csv("data/constructors.csv")
driver_standings_df = pd.read_csv("data/driver_standings.csv")
drivers_df = pd.read_csv("data/drivers.csv")
lap_times_df = pd.read_csv("data/lap_times.csv")
pit_stops_df = pd.read_csv("data/pit_stops.csv")
qualifying_df = pd.read_csv("data/qualifying.csv")
races_df = pd.read_csv("data/races.csv")
results_df = pd.read_csv("data/results.csv")
seasons_df = pd.read_csv("data/seasons.csv")
sprint_res_df = pd.read_csv("data/sprint_results.csv")
status_df = pd.read_csv("data/status.csv")
races_with_weather_df = pd.read_csv("data/races_with_weather.csv")
races_with_dummies_df = pd.read_csv("data/races_with_dummies.csv")
tyre_data_ID_df = pd.read_csv("data/tyre_data_drRef.csv")



In [39]:
pit_stops_df.columns

Index(['raceId', 'driverId', 'stop', 'lap', 'time', 'duration',
       'milliseconds'],
      dtype='object')

- We will be using 7 dataframes to prepare for our Machine Learning model. They are the following:

- 1. tyre_data_ID_df x
- 2. circuits_df x
- 3. drivers_df x
- 4. races_with_dummies_df x
- 5. pit_stops_df x
- 6. results_df x
- 7. lap_times_df x

In [40]:
tyre_data_ID_df.head() 

Unnamed: 0            Driver         GP       Tyres  From  To  #Laps  year   
0           0     Jenson Button  Australia   Soft Used     1  16     16  2012  \
1           1     Jenson Button  Australia  Medium New    17  36     20  2012   
2           2     Jenson Button  Australia  Medium New    37  58     22  2012   
3           3  Sebastian Vettel  Australia   Soft Used     1  16     16  2012   
4           4  Sebastian Vettel  Australia   Soft Used    17  37     21  2012   

   location  raceId  driverId driverRef  
0  Adelaide   860.0      18.0    button  
1  Adelaide   860.0      18.0    button  
2  Adelaide   860.0      18.0    button  
3  Adelaide   860.0      20.0    vettel  
4  Adelaide   860.0      20.0    vettel

In [41]:
tyre_data_ID_df.Tyres.unique()


array(['Soft Used', 'Medium New', 'Soft New', 'Medium Used',
       'Intermediate New', 'Wet New', 'Hard New', 'Intermediate Used',
       'Lluvia Extrema Usado', 'Hard Used', 'Supersoft Used',
       'Supersoft New', 'Ultrasoft New', 'Ultrasoft Used',
       'Hiper Blando Usado', 'Hiper Blando Nuevo'], dtype=object)

- We can see from the unique values of the Tyres column that there are 3 tyres written in Spanish, these is due to the fact that the data that was scrapped was from a Spanish Formula 1 website (https://www.f1cfa.com/f1-tyres-statistics.asp?t=2011&gpn=All&tipo=All&driver=All)

In [42]:
# change spanish words to english / have to do it before the processing - should be better

tyres_mapping = {
    'Hiper Blando Usado': 'Hyper Soft',
    'Hiper Blando Nuevo': 'Hyper Soft',
    'Lluvia Extrema Usado': 'Full Wet'
}

# Use the replace() method to update the values in the "tyres" column
tyre_data_ID_df['Tyres'] = tyre_data_ID_df['Tyres'].replace(tyres_mapping)

- Double check that the columns have been replaced "translated" correctly

In [43]:
tyre_data_ID_df.Tyres.unique()


array(['Soft Used', 'Medium New', 'Soft New', 'Medium Used',
       'Intermediate New', 'Wet New', 'Hard New', 'Intermediate Used',
       'Full Wet', 'Hard Used', 'Supersoft Used', 'Supersoft New',
       'Ultrasoft New', 'Ultrasoft Used', 'Hyper Soft'], dtype=object)

In [44]:
# SOLUTION FOR own column for each tyre value with rounds driven

# Load your tyre_data_ID_df DataFrame here

# Sort the data by driverId, raceId, and lap number
tyre_data_ID_df.sort_values(by=['driverId', 'raceId', '#Laps'], inplace=True)

# Initialize variables to keep track of pit stops
current_tyre = None
current_tyre_start_lap = None
pit_stops = []

# Iterate through the rows and record pit stops
for index, row in tyre_data_ID_df.iterrows():
    if current_tyre is None:
        current_tyre = row['Tyres']
        current_tyre_start_lap = row['#Laps']
    elif current_tyre != row['Tyres']:
        pit_stops.append({
            'driverId': row['driverId'],
            'raceId': row['raceId'],
            'Driver': row['Driver'],
            'GP': row['GP'],
            'year': row['year'],
            'location': row['location'],
            'driverRef': row['driverRef'],
            'Tyres': current_tyre,
            'Start Lap': current_tyre_start_lap,
            'End Lap': row['#Laps'] - 1
        })
        current_tyre = row['Tyres']
        current_tyre_start_lap = row['#Laps']

# Convert pit_stops list to a DataFrame
stops_df = pd.DataFrame(pit_stops)

# Group by driverId, raceId, Tyres, and other shared columns, and sum the lap numbers
consolidated_data = tyre_data_ID_df.groupby(['driverId', 'raceId', 'Driver', 'GP', 'year', 'location', 'driverRef', 'Tyres'], as_index=False)['#Laps'].sum()

# Fill missing values with 0 for laps when a driver did not use a particular tire type
consolidated_data.fillna(0, inplace=True)

# Pivot the data to have separate columns for each tire type with total laps per race
tyre_data_updated = consolidated_data.pivot_table(index=['driverId', 'raceId', 'Driver', 'GP', 'year', 'location', 'driverRef'], columns='Tyres', values='#Laps', fill_value=0).reset_index()

# Rename the columns for clarity
tyre_data_updated.rename_axis(None, axis=1, inplace=True)

# Print the consolidated data with pit stops
print(tyre_data_updated)

tyre_data_updated.to_csv("data/tyre_data_with_total_laps_per_race.csv", index=False)


      driverId  raceId               Driver             GP  year   
0          1.0   860.0       Lewis Hamilton      Australia  2012  \
1          1.0   861.0       Lewis Hamilton       Malaysia  2012   
2          1.0   863.0       Lewis Hamilton        Bahrain  2012   
3          1.0   864.0       Lewis Hamilton          Spain  2012   
4          1.0   865.0       Lewis Hamilton         Monaco  2012   
5          1.0   873.0       Lewis Hamilton      Singapore  2012   
6          1.0   874.0       Lewis Hamilton          Japan  2012   
7          1.0   875.0       Lewis Hamilton          Korea  2012   
8          1.0   876.0       Lewis Hamilton          India  2012   
9          1.0   878.0       Lewis Hamilton  United States  2012   
10         1.0   879.0       Lewis Hamilton         Brazil  2012   
11         1.0   880.0       Lewis Hamilton      Australia  2013   
12         1.0   881.0       Lewis Hamilton       Malaysia  2013   
13         1.0   883.0       Lewis Hamilton     

In [45]:
tyre_data_updated.head()

driverId  raceId          Driver         GP  year      location driverRef   
0       1.0   860.0  Lewis Hamilton  Australia  2012      Adelaide  hamilton  \
1       1.0   861.0  Lewis Hamilton   Malaysia  2012  Kuala Lumpur  hamilton   
2       1.0   863.0  Lewis Hamilton    Bahrain  2012        Sakhir  hamilton   
3       1.0   864.0  Lewis Hamilton      Spain  2012     Barcelona  hamilton   
4       1.0   865.0  Lewis Hamilton     Monaco  2012   Monte-Carlo  hamilton   

   Full Wet  Hard New  Hard Used  Hyper Soft  Intermediate New   
0         0         0          0           0                 0  \
1         0         0          0           0                30   
2         0         0          0           0                 0   
3         0        52          0           0                 0   
4         0         0          0           0                 0   

   Intermediate Used  Medium New  Medium Used  Soft New  Soft Used   
0                  0          41            0         0         17  \
1                  0           0           17         0          0   
2                  0          35           13         0          9   
3                  0           0            0         0         14   
4                  0           0            0        29          0   

   Supersoft New  Supersoft Used  Ultrasoft New  Ultrasoft Used  Wet New  
0              0               0              0               0        0  
1              0               0              0               0        9  
2              0               0              0               0        0  
3              0               0              0               0        0  
4              0              49              0               0        0

In [46]:
races_with_dummies_df.head()

raceId  year  round  circuitId                   name        date   
0       1  2009      1          1  Australian Grand Prix  2009-03-29  \
1       2  2009      2          2   Malaysian Grand Prix  2009-04-05   
2       3  2009      3         17     Chinese Grand Prix  2009-04-19   
3       4  2009      4          3     Bahrain Grand Prix  2009-04-26   
4       5  2009      5          4     Spanish Grand Prix  2009-05-10   

       time                                                url fp1_date   
0  06:00:00  http://en.wikipedia.org/wiki/2009_Australian_G...       \N  \
1  09:00:00  http://en.wikipedia.org/wiki/2009_Malaysian_Gr...       \N   
2  07:00:00  http://en.wikipedia.org/wiki/2009_Chinese_Gran...       \N   
3  12:00:00  http://en.wikipedia.org/wiki/2009_Bahrain_Gran...       \N   
4  12:00:00  http://en.wikipedia.org/wiki/2009_Spanish_Gran...       \N   

  fp1_time fp2_date fp2_time fp3_date fp3_time quali_date quali_time   
0       \N       \N       \N       \N       \N         \N         \N  \
1       \N       \N       \N       \N       \N         \N         \N   
2       \N       \N       \N       \N       \N         \N         \N   
3       \N       \N       \N       \N       \N         \N         \N   
4       \N       \N       \N       \N       \N         \N         \N   

  sprint_date sprint_time weather_category  weather_cloudy  weather_cold   
0          \N          \N     weather_warm           False         False  \
1          \N          \N      weather_dry           False         False   
2          \N          \N      weather_wet           False         False   
3          \N          \N     weather_warm           False         False   
4          \N          \N     weather_warm           False         False   

   weather_dry  weather_unknown  weather_warm  weather_wet  
0        False            False          True        False  
1         True            False         False        False  
2        False            False         False         True  
3        False            False          True        False  
4        False            False          True        False

#### Merging the dataframes


In [47]:
# Merge the tyre data with the races with dummies (includes the already scraped weather categories)

part_1 = pd.merge(tyre_data_updated, races_with_dummies_df, on="raceId")

part_1.head()

driverId  raceId             Driver         GP  year_x  location   
0       1.0   860.0     Lewis Hamilton  Australia    2012  Adelaide  \
1       3.0   860.0       Nico Rosberg  Australia    2012  Adelaide   
2       4.0   860.0    Fernando Alonso  Australia    2012  Adelaide   
3       5.0   860.0  Heikki Kovalainen  Australia    2012  Adelaide   
4       8.0   860.0     Kimi Räikkönen  Australia    2012  Adelaide   

        driverRef  Full Wet  Hard New  Hard Used  Hyper Soft   
0        hamilton         0         0          0           0  \
1         rosberg         0         0          0           0   
2          alonso         0         0          0           0   
3      kovalainen         0         0          0           0   
4  kimi raikkonen         0         0          0           0   

   Intermediate New  Intermediate Used  Medium New  Medium Used  Soft New   
0                 0                  0          41            0         0  \
1                 0                  0          27            0         0   
2                 0                  0          45            0         0   
3                 0                  0          23            1        14   
4                 0                  0          21            0        37   

   Soft Used  Supersoft New  Supersoft Used  Ultrasoft New  Ultrasoft Used   
0         17              0               0              0               0  \
1         31              0               0              0               0   
2         13              0               0              0               0   
3          0              0               0              0               0   
4          0              0               0              0               0   

   Wet New  year_y  round  circuitId                   name        date   
0        0    2012      1          1  Australian Grand Prix  2012-03-18  \
1        0    2012      1          1  Australian Grand Prix  2012-03-18   
2        0    2012      1          1  Australian Grand Prix  2012-03-18   
3        0    2012      1          1  Australian Grand Prix  2012-03-18   
4        0    2012      1          1  Australian Grand Prix  2012-03-18   

       time                                                url fp1_date   
0  06:00:00  http://en.wikipedia.org/wiki/2012_Australian_G...       \N  \
1  06:00:00  http://en.wikipedia.org/wiki/2012_Australian_G...       \N   
2  06:00:00  http://en.wikipedia.org/wiki/2012_Australian_G...       \N   
3  06:00:00  http://en.wikipedia.org/wiki/2012_Australian_G...       \N   
4  06:00:00  http://en.wikipedia.org/wiki/2012_Australian_G...       \N   

  fp1_time fp2_date fp2_time fp3_date fp3_time quali_date quali_time   
0       \N       \N       \N       \N       \N         \N         \N  \
1       \N       \N       \N       \N       \N         \N         \N   
2       \N       \N       \N       \N       \N         \N         \N   
3       \N       \N       \N       \N       \N         \N         \N   
4       \N       \N       \N       \N       \N         \N         \N   

  sprint_date sprint_time weather_category  weather_cloudy  weather_cold   
0          \N          \N     weather_warm           False         False  \
1          \N          \N     weather_warm           False         False   
2          \N          \N     weather_warm           False         False   
3          \N          \N     weather_warm           False         False   
4          \N          \N     weather_warm           False         False   

   weather_dry  weather_unknown  weather_warm  weather_wet  
0        False            False          True        False  
1        False            False          True        False  
2        False            False          True        False  
3        False            False          True        False  
4        False            False          True        False

##### From the above dataframe we can see that some columns are not useful to us and can be dropped. Those columns are:

- Driver -  we already have the driverRef
- Name -  which is the name of the GP, we already have a GP column
- Time - the starting time of the race (local time) is of no interest to us
- URL - Wikipedia pages of the Grand Prixs
- All columns from fp1 to sprint_time can be dropped
- weather_category is the source for creating dummies
- weather_unknown could be dropped as well because it is a dummy variable
- year_y - because we already have a column called year_x
- Date column
- Rounds column


In [48]:
columns_to_drop = ['Driver', 'name', 'time','url','fp1_date','fp1_time','fp2_date','fp2_time','fp3_date','fp3_time','quali_date','quali_time','sprint_date','year_y','sprint_time','date','weather_category', 'round','weather_unknown']

part_1_new = part_1.drop(columns=columns_to_drop)

In [49]:
part_1_new.head()

driverId  raceId         GP  year_x  location       driverRef  Full Wet   
0       1.0   860.0  Australia    2012  Adelaide        hamilton         0  \
1       3.0   860.0  Australia    2012  Adelaide         rosberg         0   
2       4.0   860.0  Australia    2012  Adelaide          alonso         0   
3       5.0   860.0  Australia    2012  Adelaide      kovalainen         0   
4       8.0   860.0  Australia    2012  Adelaide  kimi raikkonen         0   

   Hard New  Hard Used  Hyper Soft  Intermediate New  Intermediate Used   
0         0          0           0                 0                  0  \
1         0          0           0                 0                  0   
2         0          0           0                 0                  0   
3         0          0           0                 0                  0   
4         0          0           0                 0                  0   

   Medium New  Medium Used  Soft New  Soft Used  Supersoft New   
0          41            0         0         17              0  \
1          27            0         0         31              0   
2          45            0         0         13              0   
3          23            1        14          0              0   
4          21            0        37          0              0   

   Supersoft Used  Ultrasoft New  Ultrasoft Used  Wet New  circuitId   
0               0              0               0        0          1  \
1               0              0               0        0          1   
2               0              0               0        0          1   
3               0              0               0        0          1   
4               0              0               0        0          1   

   weather_cloudy  weather_cold  weather_dry  weather_warm  weather_wet  
0           False         False        False          True        False  
1           False         False        False          True        False  
2           False         False        False          True        False  
3           False         False        False          True        False  
4           False         False        False          True        False

In [50]:
# Merge the part_1_new with the circuits_df and use circuitId as key

part_2 = pd.merge(part_1_new, circuits_df, on="circuitId")



In [51]:
part_2.head()

driverId  raceId         GP  year_x location_x       driverRef  Full Wet   
0       1.0   860.0  Australia    2012   Adelaide        hamilton         0  \
1       3.0   860.0  Australia    2012   Adelaide         rosberg         0   
2       4.0   860.0  Australia    2012   Adelaide          alonso         0   
3       5.0   860.0  Australia    2012   Adelaide      kovalainen         0   
4       8.0   860.0  Australia    2012   Adelaide  kimi raikkonen         0   

   Hard New  Hard Used  Hyper Soft  Intermediate New  Intermediate Used   
0         0          0           0                 0                  0  \
1         0          0           0                 0                  0   
2         0          0           0                 0                  0   
3         0          0           0                 0                  0   
4         0          0           0                 0                  0   

   Medium New  Medium Used  Soft New  Soft Used  Supersoft New   
0          41            0         0         17              0  \
1          27            0         0         31              0   
2          45            0         0         13              0   
3          23            1        14          0              0   
4          21            0        37          0              0   

   Supersoft Used  Ultrasoft New  Ultrasoft Used  Wet New  circuitId   
0               0              0               0        0          1  \
1               0              0               0        0          1   
2               0              0               0        0          1   
3               0              0               0        0          1   
4               0              0               0        0          1   

   weather_cloudy  weather_cold  weather_dry  weather_warm  weather_wet   
0           False         False        False          True        False  \
1           False         False        False          True        False   
2           False         False        False          True        False   
3           False         False        False          True        False   
4           False         False        False          True        False   

    circuitRef                            name location_y    country      lat   
0  albert_park  Albert Park Grand Prix Circuit  Melbourne  Australia -37.8497  \
1  albert_park  Albert Park Grand Prix Circuit  Melbourne  Australia -37.8497   
2  albert_park  Albert Park Grand Prix Circuit  Melbourne  Australia -37.8497   
3  albert_park  Albert Park Grand Prix Circuit  Melbourne  Australia -37.8497   
4  albert_park  Albert Park Grand Prix Circuit  Melbourne  Australia -37.8497   

       lng alt                                                url  
0  144.968  10  http://en.wikipedia.org/wiki/Melbourne_Grand_P...  
1  144.968  10  http://en.wikipedia.org/wiki/Melbourne_Grand_P...  
2  144.968  10  http://en.wikipedia.org/wiki/Melbourne_Grand_P...  
3  144.968  10  http://en.wikipedia.org/wiki/Melbourne_Grand_P...  
4  144.968  10  http://en.wikipedia.org/wiki/Melbourne_Grand_P...

- We can see from the above merged dataframe that some columns can also be dropped. For example location_x is incorrect as thr Australian Gran Prix has always been held in Melbourne (Albert Park), therefore we will keep location_y

- location_x
- name
- lat, lng, alt, url

We have dropped the coordinates of each race circuit as we don't plan to use it at the moment. But further on in might come in handy to plot geographical graphs of the race circuits and show how drivers might have a winning advantage if they raced in their hme city


In [52]:
columns_to_drop_2 = ['location_x','name', 'lat','url','lng','alt']

part_2_new = part_2.drop(columns=columns_to_drop_2)

In [53]:
part_2_new.head()

driverId  raceId         GP  year_x       driverRef  Full Wet  Hard New   
0       1.0   860.0  Australia    2012        hamilton         0         0  \
1       3.0   860.0  Australia    2012         rosberg         0         0   
2       4.0   860.0  Australia    2012          alonso         0         0   
3       5.0   860.0  Australia    2012      kovalainen         0         0   
4       8.0   860.0  Australia    2012  kimi raikkonen         0         0   

   Hard Used  Hyper Soft  Intermediate New  Intermediate Used  Medium New   
0          0           0                 0                  0          41  \
1          0           0                 0                  0          27   
2          0           0                 0                  0          45   
3          0           0                 0                  0          23   
4          0           0                 0                  0          21   

   Medium Used  Soft New  Soft Used  Supersoft New  Supersoft Used   
0            0         0         17              0               0  \
1            0         0         31              0               0   
2            0         0         13              0               0   
3            1        14          0              0               0   
4            0        37          0              0               0   

   Ultrasoft New  Ultrasoft Used  Wet New  circuitId  weather_cloudy   
0              0               0        0          1           False  \
1              0               0        0          1           False   
2              0               0        0          1           False   
3              0               0        0          1           False   
4              0               0        0          1           False   

   weather_cold  weather_dry  weather_warm  weather_wet   circuitRef   
0         False        False          True        False  albert_park  \
1         False        False          True        False  albert_park   
2         False        False          True        False  albert_park   
3         False        False          True        False  albert_park   
4         False        False          True        False  albert_park   

  location_y    country  
0  Melbourne  Australia  
1  Melbourne  Australia  
2  Melbourne  Australia  
3  Melbourne  Australia  
4  Melbourne  Australia

In [54]:
# Merge the part_2_new with the result_df and use raceId, driverId as keys

part_3 = pd.merge(part_2_new, results_df, on= ["raceId","driverId"])

In [55]:
part_3.head(30)

driverId  raceId         GP  year_x           driverRef  Full Wet   
0        1.0   860.0  Australia    2012            hamilton         0  \
1        3.0   860.0  Australia    2012             rosberg         0   
2        4.0   860.0  Australia    2012              alonso         0   
3        5.0   860.0  Australia    2012          kovalainen         0   
4        8.0   860.0  Australia    2012      kimi raikkonen         0   
5       10.0   860.0  Australia    2012               glock         0   
6       13.0   860.0  Australia    2012               massa         0   
7       17.0   860.0  Australia    2012              webber         0   
8       18.0   860.0  Australia    2012              button         0   
9       20.0   860.0  Australia    2012              vettel         0   
10      30.0   860.0  Australia    2012  michael_schumacher         0   
11     154.0   860.0  Australia    2012            grosjean         0   
12     155.0   860.0  Australia    2012           kobayashi         0   
13     807.0   860.0  Australia    2012          hulkenberg         0   
14     808.0   860.0  Australia    2012              petrov         0   
15     813.0   860.0  Australia    2012           maldonado         0   
16     814.0   860.0  Australia    2012               resta         0   
17     815.0   860.0  Australia    2012               perez         0   
18     817.0   860.0  Australia    2012           ricciardo         0   
19     818.0   860.0  Australia    2012              vergne         0   
20     819.0   860.0  Australia    2012                 pic         0   
21       1.0   880.0  Australia    2013            hamilton         0   
22       3.0   880.0  Australia    2013             rosberg         0   
23       4.0   880.0  Australia    2013              alonso         0   
24       8.0   880.0  Australia    2013      kimi raikkonen         0   
25      13.0   880.0  Australia    2013               massa         0   
26      16.0   880.0  Australia    2013               sutil         0   
27      17.0   880.0  Australia    2013              webber         0   
28      18.0   880.0  Australia    2013              button         0   
29      20.0   880.0  Australia    2013              vettel         0   

    Hard New  Hard Used  Hyper Soft  Intermediate New  Intermediate Used   
0          0          0           0                 0                  0  \
1          0          0           0                 0                  0   
2          0          0           0                 0                  0   
3          0          0           0                 0                  0   
4          0          0           0                 0                  0   
5          0          0           0                 0                  0   
6          0          0           0                 0                  0   
7          0          0           0                 0                  0   
8          0          0           0                 0                  0   
9          0          0           0                 0                  0   
10         0          0           0                 0                  0   
11         0          0           0                 0                  0   
12         0          0           0                 0                  0   
13         0          0           0                 0                  0   
14         0          0           0                 0                  0   
15         0          0           0                 0                  0   
16         0          0           0                 0                  0   
17         0          0           0                 0                  0   
18         0          0           0                 0                  0   
19         0          0           0                 0                  0   
20         0          0           0                 0                  0   
21         0          0           0                 0               

We can see that there are three columns named: position, positionText and positionOrder

position: the final position in the race
positionText: similar to the position but includes the information of retired drivers (R), could get information of reason of retirement from statusID (e.g. 4 = collision)
positionOrder: it has the final positions but also including the positions of the drivers who retired

We could technically drop the position column.

In [56]:
columns_to_drop_3 = ['position']

part_3_new = part_3.drop(columns=columns_to_drop_3)

In [57]:
part_3_new.head()

driverId  raceId         GP  year_x       driverRef  Full Wet  Hard New   
0       1.0   860.0  Australia    2012        hamilton         0         0  \
1       3.0   860.0  Australia    2012         rosberg         0         0   
2       4.0   860.0  Australia    2012          alonso         0         0   
3       5.0   860.0  Australia    2012      kovalainen         0         0   
4       8.0   860.0  Australia    2012  kimi raikkonen         0         0   

   Hard Used  Hyper Soft  Intermediate New  Intermediate Used  Medium New   
0          0           0                 0                  0          41  \
1          0           0                 0                  0          27   
2          0           0                 0                  0          45   
3          0           0                 0                  0          23   
4          0           0                 0                  0          21   

   Medium Used  Soft New  Soft Used  Supersoft New  Supersoft Used   
0            0         0         17              0               0  \
1            0         0         31              0               0   
2            0         0         13              0               0   
3            1        14          0              0               0   
4            0        37          0              0               0   

   Ultrasoft New  Ultrasoft Used  Wet New  circuitId  weather_cloudy   
0              0               0        0          1           False  \
1              0               0        0          1           False   
2              0               0        0          1           False   
3              0               0        0          1           False   
4              0               0        0          1           False   

   weather_cold  weather_dry  weather_warm  weather_wet   circuitRef   
0         False        False          True        False  albert_park  \
1         False        False          True        False  albert_park   
2         False        False          True        False  albert_park   
3         False        False          True        False  albert_park   
4         False        False          True        False  albert_park   

  location_y    country  resultId  constructorId number  grid positionText   
0  Melbourne  Australia     21234              1      4     1            3  \
1  Melbourne  Australia     21243            131      8     7           12   
2  Melbourne  Australia     21236              6      5    12            5   
3  Melbourne  Australia     21249            207     20    18            R   
4  Melbourne  Australia     21238            208      9    17            7   

   positionOrder  points  laps     time milliseconds fastestLap rank   
0              3    15.0    58   +4.075      5653640         57    4  \
1             12     0.0    58  +57.642      5707207         53   14   
2              5    10.0    58  +21.565      5671130         52    7   
3             18     0.0    38       \N           \N         26   17   
4              7     6.0    58  +38.014      5687579         50   11   

  fastestLapTime fastestLapSpeed  statusId  
0       1:29.538         213.214         1  
1       1:30.931         209.948         1  
2       1:30.277         211.469         1  
3       1:33.693         203.759        22  
4       1:30.759         210.346         1

In [58]:
# Merge the part_3_new with the drivers_df and use driverId as keys

part_4 = pd.merge(part_3_new, drivers_df, on= ["driverId"])

In [59]:
part_4.head(20)

driverId  raceId         GP  year_x driverRef_x  Full Wet  Hard New   
0        1.0   860.0  Australia    2012    hamilton         0         0  \
1        1.0   880.0  Australia    2013    hamilton         0         0   
2        1.0   900.0  Australia    2014    hamilton         0         0   
3        1.0   926.0  Australia    2015    hamilton         0         0   
4        1.0   948.0  Australia    2016    hamilton         0         0   
5        1.0   969.0  Australia    2017    hamilton         0         0   
6        1.0   989.0  Australia    2018    hamilton         0         0   
7        1.0  1010.0  Australia    2019    hamilton         0         0   
8        1.0  1076.0  Australia    2022    hamilton         0        36   
9        1.0   861.0   Malaysia    2012    hamilton         0         0   
10       1.0   881.0   Malaysia    2013    hamilton         0        11   
11       1.0   901.0   Malaysia    2014    hamilton         0         5   
12       1.0   927.0   Malaysia    2015    hamilton         0        38   
13       1.0   963.0   Malaysia    2016    hamilton         0        20   
14       1.0   983.0   Malaysia    2017    hamilton         0         0   
15       1.0   863.0    Bahrain    2012    hamilton         0         0   
16       1.0   883.0    Bahrain    2013    hamilton         0        35   
17       1.0   902.0    Bahrain    2014    hamilton         0         0   
18       1.0   929.0    Bahrain    2015    hamilton         0         0   
19       1.0   949.0    Bahrain    2016    hamilton         0         0   

    Hard Used  Hyper Soft  Intermediate New  Intermediate Used  Medium New   
0           0           0                 0                  0          41  \
1           0           0                 0                  0          45   
2           0           0                 0                  0           0   
3           0           0                 0                  0          33   
4           0           0                 0                  0          41   
5           0           0                 0                  0           0   
6           0           0                 0                  0           0   
7           0           0                 0                  0          43   
8           0           0                 0                  0          22   
9           0           0                30                  0           0   
10          0           0                 7                  0          23   
11          0           0                 0                  0          51   
12          0           0                 0                  0          14   
13          0           0                 0                  0           0   
14          0           0                 0                  0           0   
15          0           0                 0                  0          35   
16          0           0                 0                  0           0   
17          0           0                 0                  0          16   
18          0           0                 0                  0          24   
19          0           0                 0                  0          15   

    Medium Used  Soft New  Soft Used  Supersoft New  Supersoft Used   
0             0         0         17              0               0  \
1             0         0          0              0              13   
2             0         2          0              0               0   
3             0         0         25              0               0   
4             0         0          0              0              16   
5             0        40          0              0               0   
6             0        39          0              0               0   
7             0         0         15              0               0   
8             0         0          0              0               0   
9            17         0          0              0               0   
10      

We can see that there are three columns named: driverRef_y,number_y, code, forename, surname, dob, url

- driverRef_y: We already have a unique driver reference called driverRef_x
- number_y: The number of the drive, but we have the driverId instead
- code: Abbreviated code for the driver's name
- forename, surname, dob: Full name of driver and date of birth are of no relevance
- url: Wikipedia page for the driver

In [60]:
columns_to_drop_4 = ['driverRef_y',	'number_y',	'code',	'forename', 'surname','dob', 'url']

part_4_new = part_4.drop(columns=columns_to_drop_4)

In [61]:
part_4_new.head(20)

driverId  raceId         GP  year_x driverRef_x  Full Wet  Hard New   
0        1.0   860.0  Australia    2012    hamilton         0         0  \
1        1.0   880.0  Australia    2013    hamilton         0         0   
2        1.0   900.0  Australia    2014    hamilton         0         0   
3        1.0   926.0  Australia    2015    hamilton         0         0   
4        1.0   948.0  Australia    2016    hamilton         0         0   
5        1.0   969.0  Australia    2017    hamilton         0         0   
6        1.0   989.0  Australia    2018    hamilton         0         0   
7        1.0  1010.0  Australia    2019    hamilton         0         0   
8        1.0  1076.0  Australia    2022    hamilton         0        36   
9        1.0   861.0   Malaysia    2012    hamilton         0         0   
10       1.0   881.0   Malaysia    2013    hamilton         0        11   
11       1.0   901.0   Malaysia    2014    hamilton         0         5   
12       1.0   927.0   Malaysia    2015    hamilton         0        38   
13       1.0   963.0   Malaysia    2016    hamilton         0        20   
14       1.0   983.0   Malaysia    2017    hamilton         0         0   
15       1.0   863.0    Bahrain    2012    hamilton         0         0   
16       1.0   883.0    Bahrain    2013    hamilton         0        35   
17       1.0   902.0    Bahrain    2014    hamilton         0         0   
18       1.0   929.0    Bahrain    2015    hamilton         0         0   
19       1.0   949.0    Bahrain    2016    hamilton         0         0   

    Hard Used  Hyper Soft  Intermediate New  Intermediate Used  Medium New   
0           0           0                 0                  0          41  \
1           0           0                 0                  0          45   
2           0           0                 0                  0           0   
3           0           0                 0                  0          33   
4           0           0                 0                  0          41   
5           0           0                 0                  0           0   
6           0           0                 0                  0           0   
7           0           0                 0                  0          43   
8           0           0                 0                  0          22   
9           0           0                30                  0           0   
10          0           0                 7                  0          23   
11          0           0                 0                  0          51   
12          0           0                 0                  0          14   
13          0           0                 0                  0           0   
14          0           0                 0                  0           0   
15          0           0                 0                  0          35   
16          0           0                 0                  0           0   
17          0           0                 0                  0          16   
18          0           0                 0                  0          24   
19          0           0                 0                  0          15   

    Medium Used  Soft New  Soft Used  Supersoft New  Supersoft Used   
0             0         0         17              0               0  \
1             0         0          0              0              13   
2             0         2          0              0               0   
3             0         0         25              0               0   
4             0         0          0              0              16   
5             0        40          0              0               0   
6             0        39          0              0               0   
7             0         0         15              0               0   
8             0         0          0              0               0   
9            17         0          0              0               0   
10      

In [62]:
pit_stops_df.columns

Index(['raceId', 'driverId', 'stop', 'lap', 'time', 'duration',
       'milliseconds'],
      dtype='object')

In [63]:


# Replace this with your actual data import method

# Create a DataFrame for pit stops with 'stop' equal to 2
pit_stop_2_df = pit_stops_df[pit_stops_df['stop'] == 2]

# Rename columns in the pit_stop_2_df to avoid conflicts when merging
pit_stop_2_df = pit_stop_2_df.rename(columns={
    'lap': 'pit_stop_2_lap',
    'time': 'pit_stop_2_time',
    'duration': 'pit_stop_2_duration',
    'milliseconds': 'pit_stop_2_milliseconds'
}) 

# Merge the pit_stop_2_df with the original DataFrame using raceId and driverId
merged_df = pit_stops_df.merge(pit_stop_2_df[['raceId', 'driverId', 'pit_stop_2_lap', 'pit_stop_2_time', 'pit_stop_2_duration', 'pit_stop_2_milliseconds']], on=['raceId', 'driverId'], how='left')

# Fill NaN values with appropriate values (0 in this case)
merged_df = merged_df.fillna(0)

# Drop the duplicate rows with the same raceId and driverId
merged_df = merged_df.drop_duplicates(subset=['raceId', 'driverId'])

# Reset index if needed
merged_df = merged_df.reset_index(drop=True)

# Print the resulting DataFrame
print(merged_df)

      raceId  driverId  stop  lap      time   duration  milliseconds   
0        841       153     1    1  17:05:23     26.898         26898  \
1        841        30     1    1  17:05:52     25.021         25021   
2        841        17     1   11  17:20:48     23.426         23426   
3        841         4     1   12  17:22:34     23.251         23251   
4        841        13     1   13  17:24:10     23.842         23842   
5        841        22     1   13  17:24:29     23.643         23643   
6        841        20     1   14  17:25:17     22.603         22603   
7        841       814     1   14  17:26:03     24.863         24863   
8        841       816     1   14  17:26:50     25.259         25259   
9        841        67     1   15  17:27:34     25.342         25342   
10       841         2     1   15  17:27:41     22.994         22994   
11       841         1     1   16  17:28:24     23.227         23227   
12       841       808     1   16  17:28:39     24.535         2

In [64]:
# Define a list of stop values to consider
stop_values = [1, 2, 3, 4, 5, 6]

# Create an empty DataFrame to store the merged data
merged_df = pit_stops_df.copy()

# Iterate through stop values and merge the corresponding DataFrames
for stop_value in stop_values:
    # Filter the DataFrame for the current stop value
    pit_stop_df = pit_stops_df[pit_stops_df['stop'] == stop_value]
    
    # Rename columns to avoid conflicts when merging
    pit_stop_df = pit_stop_df.rename(columns={
        'lap': f'pit_stop_{stop_value}_lap',
        'time': f'pit_stop_{stop_value}_time',
        'duration': f'pit_stop_{stop_value}_duration',
        'milliseconds': f'pit_stop_{stop_value}_milliseconds'
    })

    # Merge the current pit stop data with the merged DataFrame
    merged_df = merged_df.merge(pit_stop_df[['raceId', 'driverId', f'pit_stop_{stop_value}_lap', f'pit_stop_{stop_value}_time', f'pit_stop_{stop_value}_duration', f'pit_stop_{stop_value}_milliseconds']], on=['raceId', 'driverId'], how='left')

# Fill NaN values with appropriate values (0 in this case)
merged_df = merged_df.fillna(0)

# Drop the duplicate rows with the same raceId and driverId
merged_df = merged_df.drop_duplicates(subset=['raceId', 'driverId'])

# Reset index if needed
merged_df = merged_df.reset_index(drop=True)

# Print the resulting DataFrame
print(merged_df)


      raceId  driverId  stop  lap      time   duration  milliseconds   
0        841       153     1    1  17:05:23     26.898         26898  \
1        841        30     1    1  17:05:52     25.021         25021   
2        841        17     1   11  17:20:48     23.426         23426   
3        841         4     1   12  17:22:34     23.251         23251   
4        841        13     1   13  17:24:10     23.842         23842   
5        841        22     1   13  17:24:29     23.643         23643   
6        841        20     1   14  17:25:17     22.603         22603   
7        841       814     1   14  17:26:03     24.863         24863   
8        841       816     1   14  17:26:50     25.259         25259   
9        841        67     1   15  17:27:34     25.342         25342   
10       841         2     1   15  17:27:41     22.994         22994   
11       841         1     1   16  17:28:24     23.227         23227   
12       841       808     1   16  17:28:39     24.535         2

In [65]:
merged_df.head()

raceId  driverId  stop  lap      time duration  milliseconds   
0     841       153     1    1  17:05:23   26.898         26898  \
1     841        30     1    1  17:05:52   25.021         25021   
2     841        17     1   11  17:20:48   23.426         23426   
3     841         4     1   12  17:22:34   23.251         23251   
4     841        13     1   13  17:24:10   23.842         23842   

   pit_stop_1_lap pit_stop_1_time pit_stop_1_duration   
0             1.0        17:05:23              26.898  \
1             1.0        17:05:52              25.021   
2            11.0        17:20:48              23.426   
3            12.0        17:22:34              23.251   
4            13.0        17:24:10              23.842   

   pit_stop_1_milliseconds  pit_stop_2_lap pit_stop_2_time   
0                  26898.0            17.0        17:31:06  \
1                  25021.0            17.0        17:32:08   
2                  23426.0            26.0        17:44:29   
3                  23251.0            27.0        17:46:04   
4                  23842.0            31.0        17:52:28   

  pit_stop_2_duration  pit_stop_2_milliseconds  pit_stop_3_lap   
0              24.463                  24463.0            35.0  \
1              23.988                  23988.0             0.0   
2              22.520                  22520.0            41.0   
3              24.733                  24733.0            42.0   
4              24.500                  24500.0            48.0   

  pit_stop_3_time pit_stop_3_duration  pit_stop_3_milliseconds   
0        17:59:45              26.348                  26348.0  \
1               0                   0                      0.0   
2        18:07:37              26.230                  26230.0   
3        18:09:08              24.181                  24181.0   
4        18:18:54              24.095                  24095.0   

   pit_stop_4_lap pit_stop_4_time pit_stop_4_duration   
0             0.0               0                   0  \
1             0.0               0                   0   
2             0.0               0                   0   
3             0.0               0                   0   
4             0.0               0                   0   

   pit_stop_4_milliseconds  pit_stop_5_lap pit_stop_5_time   
0                      0.0             0.0               0  \
1                      0.0             0.0               0   
2                      0.0             0.0               0   
3                      0.0             0.0               0   
4                      0.0             0.0               0   

  pit_stop_5_duration  pit_stop_5_milliseconds  pit_stop_6_lap   
0                   0                      0.0             0.0  \
1                   0                      0.0             0.0   
2                   0                      0.0             0.0   
3                   0                      0.0             0.0   
4                   0                      0.0             0.0   

  pit_stop_6_time pit_stop_6_duration  pit_stop_6_milliseconds  
0               0                   0                      0.0  
1               0                   0                      0.0  
2               0                   0                      0.0  
3               0                   0                      0.0  
4               0                   0                      0.0

In [66]:
# Merge the part_4_new with the pit_stops_df and use driverId and raceId as keys

part_5 = pd.merge(part_4_new, merged_df, on= ["driverId", "raceId"])

In [67]:
part_5.head(20)

driverId  raceId         GP  year_x driverRef_x  Full Wet  Hard New   
0        1.0   860.0  Australia    2012    hamilton         0         0  \
1        1.0   880.0  Australia    2013    hamilton         0         0   
2        1.0   926.0  Australia    2015    hamilton         0         0   
3        1.0   948.0  Australia    2016    hamilton         0         0   
4        1.0   969.0  Australia    2017    hamilton         0         0   
5        1.0   989.0  Australia    2018    hamilton         0         0   
6        1.0  1010.0  Australia    2019    hamilton         0         0   
7        1.0  1076.0  Australia    2022    hamilton         0        36   
8        1.0   861.0   Malaysia    2012    hamilton         0         0   
9        1.0   881.0   Malaysia    2013    hamilton         0        11   
10       1.0   901.0   Malaysia    2014    hamilton         0         5   
11       1.0   927.0   Malaysia    2015    hamilton         0        38   
12       1.0   963.0   Malaysia    2016    hamilton         0        20   
13       1.0   983.0   Malaysia    2017    hamilton         0         0   
14       1.0   863.0    Bahrain    2012    hamilton         0         0   
15       1.0   883.0    Bahrain    2013    hamilton         0        35   
16       1.0   902.0    Bahrain    2014    hamilton         0         0   
17       1.0   929.0    Bahrain    2015    hamilton         0         0   
18       1.0   949.0    Bahrain    2016    hamilton         0         0   
19       1.0   971.0    Bahrain    2017    hamilton         0         0   

    Hard Used  Hyper Soft  Intermediate New  Intermediate Used  Medium New   
0           0           0                 0                  0          41  \
1           0           0                 0                  0          45   
2           0           0                 0                  0          33   
3           0           0                 0                  0          41   
4           0           0                 0                  0           0   
5           0           0                 0                  0           0   
6           0           0                 0                  0          43   
7           0           0                 0                  0          22   
8           0           0                30                  0           0   
9           0           0                 7                  0          23   
10          0           0                 0                  0          51   
11          0           0                 0                  0          14   
12          0           0                 0                  0           0   
13          0           0                 0                  0           0   
14          0           0                 0                  0          35   
15          0           0                 0                  0           0   
16          0           0                 0                  0          16   
17          0           0                 0                  0          24   
18          0           0                 0                  0          15   
19          0           0                 0                  0           0   

    Medium Used  Soft New  Soft Used  Supersoft New  Supersoft Used   
0             0         0         17              0               0  \
1             0         0          0              0              13   
2             0         0         25              0               0   
3             0         0          0              0              16   
4             0        40          0              0               0   
5             0        39          0              0               0   
6             0         0         15              0               0   
7             0         0          0              0               0   
8            17         0          0              0               0   
9            15         0          0              0               0   
10      

For the above dataframe output we can observe that we have a few columns that will be not of much use to us:

- time_x: The time it took each driver to finish the race. The problem with is column is only keeps a timestamp for the winner of the race (Position 1) and every driver after that has an aggregated number of seconds added to the one of the driver who came in first. So basically the values are not uniform and this could cause us problems down the line. (Could be added later)
- milliseconds_x: This could be kept instead of time_x, but having hours converted into milliseconds is pretty hard to read
- number_x: the number of the drive. Not needed as we already have a unique driver identifier
- time_y: The actual timestamp of when they went in to pit. We would need the local time of each race for this, which is available but it adds another layer of complexity
- stop,	lap	time_y,	duration,milliseconds_y as we already have these columns in the merged_df (see above)

In [68]:
columns_to_drop_5 = ['time_x','milliseconds_x','number_x','stop','lap','time_y','duration','milliseconds_y']

part_5_new = part_5.drop(columns=columns_to_drop_5)

In [69]:
part_5_new.head(20)

driverId  raceId         GP  year_x driverRef_x  Full Wet  Hard New   
0        1.0   860.0  Australia    2012    hamilton         0         0  \
1        1.0   880.0  Australia    2013    hamilton         0         0   
2        1.0   926.0  Australia    2015    hamilton         0         0   
3        1.0   948.0  Australia    2016    hamilton         0         0   
4        1.0   969.0  Australia    2017    hamilton         0         0   
5        1.0   989.0  Australia    2018    hamilton         0         0   
6        1.0  1010.0  Australia    2019    hamilton         0         0   
7        1.0  1076.0  Australia    2022    hamilton         0        36   
8        1.0   861.0   Malaysia    2012    hamilton         0         0   
9        1.0   881.0   Malaysia    2013    hamilton         0        11   
10       1.0   901.0   Malaysia    2014    hamilton         0         5   
11       1.0   927.0   Malaysia    2015    hamilton         0        38   
12       1.0   963.0   Malaysia    2016    hamilton         0        20   
13       1.0   983.0   Malaysia    2017    hamilton         0         0   
14       1.0   863.0    Bahrain    2012    hamilton         0         0   
15       1.0   883.0    Bahrain    2013    hamilton         0        35   
16       1.0   902.0    Bahrain    2014    hamilton         0         0   
17       1.0   929.0    Bahrain    2015    hamilton         0         0   
18       1.0   949.0    Bahrain    2016    hamilton         0         0   
19       1.0   971.0    Bahrain    2017    hamilton         0         0   

    Hard Used  Hyper Soft  Intermediate New  Intermediate Used  Medium New   
0           0           0                 0                  0          41  \
1           0           0                 0                  0          45   
2           0           0                 0                  0          33   
3           0           0                 0                  0          41   
4           0           0                 0                  0           0   
5           0           0                 0                  0           0   
6           0           0                 0                  0          43   
7           0           0                 0                  0          22   
8           0           0                30                  0           0   
9           0           0                 7                  0          23   
10          0           0                 0                  0          51   
11          0           0                 0                  0          14   
12          0           0                 0                  0           0   
13          0           0                 0                  0           0   
14          0           0                 0                  0          35   
15          0           0                 0                  0           0   
16          0           0                 0                  0          16   
17          0           0                 0                  0          24   
18          0           0                 0                  0          15   
19          0           0                 0                  0           0   

    Medium Used  Soft New  Soft Used  Supersoft New  Supersoft Used   
0             0         0         17              0               0  \
1             0         0          0              0              13   
2             0         0         25              0               0   
3             0         0          0              0              16   
4             0        40          0              0               0   
5             0        39          0              0               0   
6             0         0         15              0               0   
7             0         0          0              0               0   
8            17         0          0              0               0   
9            15         0          0              0               0   
10      

In [70]:
# Merge the part_5_new with the merged_df (merged pit_stops_df dataframe created above, which is one unique driverId and raceId) and use driverId and raceId as keys

part_6 = pd.merge(part_5_new, merged_df, on= ["driverId", "raceId"])

In [71]:
part_6.head(20)

driverId  raceId         GP  year_x driverRef_x  Full Wet  Hard New   
0        1.0   860.0  Australia    2012    hamilton         0         0  \
1        1.0   880.0  Australia    2013    hamilton         0         0   
2        1.0   926.0  Australia    2015    hamilton         0         0   
3        1.0   948.0  Australia    2016    hamilton         0         0   
4        1.0   969.0  Australia    2017    hamilton         0         0   
5        1.0   989.0  Australia    2018    hamilton         0         0   
6        1.0  1010.0  Australia    2019    hamilton         0         0   
7        1.0  1076.0  Australia    2022    hamilton         0        36   
8        1.0   861.0   Malaysia    2012    hamilton         0         0   
9        1.0   881.0   Malaysia    2013    hamilton         0        11   
10       1.0   901.0   Malaysia    2014    hamilton         0         5   
11       1.0   927.0   Malaysia    2015    hamilton         0        38   
12       1.0   963.0   Malaysia    2016    hamilton         0        20   
13       1.0   983.0   Malaysia    2017    hamilton         0         0   
14       1.0   863.0    Bahrain    2012    hamilton         0         0   
15       1.0   883.0    Bahrain    2013    hamilton         0        35   
16       1.0   902.0    Bahrain    2014    hamilton         0         0   
17       1.0   929.0    Bahrain    2015    hamilton         0         0   
18       1.0   949.0    Bahrain    2016    hamilton         0         0   
19       1.0   971.0    Bahrain    2017    hamilton         0         0   

    Hard Used  Hyper Soft  Intermediate New  Intermediate Used  Medium New   
0           0           0                 0                  0          41  \
1           0           0                 0                  0          45   
2           0           0                 0                  0          33   
3           0           0                 0                  0          41   
4           0           0                 0                  0           0   
5           0           0                 0                  0           0   
6           0           0                 0                  0          43   
7           0           0                 0                  0          22   
8           0           0                30                  0           0   
9           0           0                 7                  0          23   
10          0           0                 0                  0          51   
11          0           0                 0                  0          14   
12          0           0                 0                  0           0   
13          0           0                 0                  0           0   
14          0           0                 0                  0          35   
15          0           0                 0                  0           0   
16          0           0                 0                  0          16   
17          0           0                 0                  0          24   
18          0           0                 0                  0          15   
19          0           0                 0                  0           0   

    Medium Used  Soft New  Soft Used  Supersoft New  Supersoft Used   
0             0         0         17              0               0  \
1             0         0          0              0              13   
2             0         0         25              0               0   
3             0         0          0              0              16   
4             0        40          0              0               0   
5             0        39          0              0               0   
6             0         0         15              0               0   
7             0         0          0              0               0   
8            17         0          0              0               0   
9            15         0          0              0               0   
10      

Let' save this last dataframe into a csv file

In [72]:
part_6.to_csv("data/ml_dataframe.csv", index=False)